### Introduction SATPy to ILWISPy

Ensure that you have installed SATPy and eventual other sitepackages required, see also the code field below. The Notebook was tested using Python version 3.9. If you use Python3.6 some SATPy functionality might not be available!
The sample data for this notebook is expected in a directory 'Intro_Satpy2ILWISPy' within this notebook folder.

In [ ]:
#load required required libraries and install sitepackages
from ctypes import *
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLdispatch.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLX.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGL.so.1.7.0')

lib1 = cdll.LoadLibrary('/opt/conda/lib/libpython3.11.so.1.0')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Gui.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Sql.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Concurrent.so.5')

!pip install satpy

In [ ]:
import datetime
import shutil
from IPython.core.display import HTML
import os
import os.path
import sys
import glob
import numpy as np
import ilwis
from satpy.scene import Scene
from satpy.resample import get_area_def
from satpy import find_files_and_readers
import warnings
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore')

In [ ]:
#use the Python function os.getcwd() to retrieve the current folder used and add a sub-folder
work_dir = os.getcwd() + '/Intro_Satpy2ILWISPy'

 #set the working directory for ILWISPy
ilwis.setWorkingCatalog(work_dir)
print(work_dir)

In [ ]:
ilwis.version()

In [ ]:
# read unzipped file, here extension *.nat
fnames = glob.glob(work_dir+'/*.nat')
print(fnames)

scn = Scene(reader='seviri_l1b_native',  filenames=fnames)

In [ ]:
scn.available_dataset_names()

In [ ]:
#get list of functions available
dir(scn)

In [ ]:
#note calibration = counts
scn.load(['VIS006'], upper_right_corner='NE', calibration='counts')
scn.keys()

In [ ]:
scn['VIS006']

In [ ]:
print(scn['VIS006'].attrs['start_time'])
print(scn['VIS006'].attrs['end_time'])

In [ ]:
print(scn)

In [ ]:
d = np.array(list(scn.values()))

In [ ]:
np.shape(d)

In [ ]:
vis006 = scn['VIS006']
vis006.attrs['area']

In [ ]:
vis006_meas = d[0]
vis006_meas_int = vis006_meas.astype(int)
print(vis006_meas_int[1600,1600])

In [ ]:
print(scn.available_composite_names())

In [ ]:
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563,envelope=-5570248.4773 5570248.4773 5567248.0742 -5567248.0742,gridsize=3712 3712,cornerofcorners=yes')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0.0, 1023.0, 0.1))
rcNew = ilwis.RasterCoverage()
rcNew.setSize(ilwis.Size(3712,3712,1))
rcNew.setGeoReference(grf)
rcNew.setDataDef(dfNum)

In [ ]:
rcNew.array2raster(vis006_meas.flatten())
rcNew.pix2value(ilwis.Pixel(1600,1600))

In [ ]:
plt.figure(figsize=(8, 8))
plt.imshow(vis006_meas, interpolation='nearest', cmap='Greys_r')
plt.show()

In [ ]:
# sub map creation
rcSelect = ilwis.do('selection',rcNew,"boundingbox(1500 1500, 2499 2499)")
print(rcSelect.size().xsize)
print(rcSelect.size().ysize)
print(rcSelect.size().zsize)
rcSelect.pix2value(ilwis.Pixel(500,500))

In [ ]:
def descriptive_statistics(raster_input):
    print('Raster size: ',raster_input.size())
    print()
    print('Map extent: ',raster_input.envelope())
    print()
    coordSys_input = raster_input.coordinateSystem()
    print('Coordinate system: ',coordSys_input.toWKT())
    print()
    print('Proj4: ',coordSys_input.toProj4())
    print()
    datadef_input = raster_input.datadef()
    print('Data type: ', datadef_input.domain())
    stats_input = raster_input.statistics(ilwis.PropertySets.pHISTOGRAM)
    print()
    print('Minimum: ',stats_input[ilwis.PropertySets.pMIN]) 
    print('Maximum: ',stats_input[ilwis.PropertySets.pMAX]) 
    print('Mean: ',stats_input[ilwis.PropertySets.pMEAN]) 
    print('No pixels - also nodata: ',stats_input[ilwis.PropertySets.pCOUNT]) 
    print('No pixels - no nodata: ',stats_input[ilwis.PropertySets.pNETTOCOUNT]) 
    print('Sum all: ',stats_input[ilwis.PropertySets.pSUM]) 

    print()
    x=[a for (a,b) in stats_input.histogram()][:-1] 
    y=[b for (a,b) in stats_input.histogram()][:-1]

    plt.plot(x,y,label='Raster Map values')
    plt.xlabel('Data Range')
    plt.ylabel('Data Frequency')
    plt.title('Raster Histogram')
    plt.legend()

In [ ]:
#execute the definition using the selected spectral channel
descriptive_statistics(rcSelect)

In [ ]:
b1s = ilwis.do('linearstretch',rcSelect, 1)
b1s = ilwis.do('setvaluerange', b1s, 0, 255, 1)

In [ ]:
#execute the definition using the selected spectral channel
descriptive_statistics(b1s)

In [ ]:
b1s.pix2value(ilwis.Pixel(500,500))

In [ ]:
b1s.store('sub_stretched.mpr')

In [ ]:
rcNew2 = ilwis.do('mapcalc', 'iff(@1>=0,@1,?)', rcNew) # remove satpy nodata

In [ ]:
rcNew2.store('vis006a.mpr')

In [ ]:
scn.available_dataset_names()

In [ ]:
scn = Scene(reader='seviri_l1b_native',  filenames=fnames)
scn.load(['VIS006'])
scn.load(['VIS008'])
scn.load(['IR_016'])

r_band = 'IR_016'
g_band = 'VIS008'
b_band = 'VIS006'
scn.load([r_band, g_band, b_band])

In [ ]:
from satpy.composites import GenericCompositor
comp = GenericCompositor('my_rgb')
my_rgb = comp((scn[r_band], scn[g_band], scn[b_band]))

In [ ]:
from satpy.writers import get_enhanced_image
plt.figure(figsize=(8,8))
img = get_enhanced_image(my_rgb)
# get DataArray out of `XRImage` object
img_data = img.data
img_data.plot.imshow(vmin=0, vmax=1, rgb='bands')

In [ ]:
scn2 = Scene(reader='seviri_l1b_native',  filenames=fnames)
scn2.load(['VIS006'])
scn2.load(['VIS008'])
scn2.load(['IR_016'])

vis006 = scn2["VIS006"]
vis008 = scn2["VIS008"]
ir_016 = scn2["IR_016"]

vis006_meas = vis006.values#[:-1:]
vis008_meas = vis008.values#[:-1:]
ir_016_meas = ir_016.values#[:-1:]

print(vis006_meas[1600,1600])
print(vis008_meas[1600,1600])
print(ir_016_meas[1600,1600])

vis006_rot = np.rot90(vis006_meas, k=2, axes=(1, 0))
vis008_rot = np.rot90(vis008_meas, k=2, axes=(1, 0))
ir_016_rot = np.rot90(ir_016_meas, k=2, axes=(1, 0))

print(vis006_rot[1600,1600])
print(vis008_rot[1600,1600])
print(ir_016_rot[1600,1600])

data = np.array([vis006_rot, vis008_rot, ir_016_rot]).flatten()

In [ ]:
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563,envelope=-5570248.4773 5570248.4773 5567248.0742 -5567248.0742,gridsize=3712 3712,cornerofcorners=yes')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0.0, 1000.0, 0.001))
rcNew2 = ilwis.RasterCoverage()
rcNew2.setSize(ilwis.Size(3712,3712,3))
rcNew2.setGeoReference(grf)
rcNew2.setDataDef(dfNum)

In [ ]:
rcNew2.array2raster(data)

In [ ]:
print(rcNew2.pix2value(ilwis.Pixel(1600,1600,0)))
print(rcNew2.pix2value(ilwis.Pixel(1600,1600,1)))
print(rcNew2.pix2value(ilwis.Pixel(1600,1600,2)))

In [ ]:
rcNew2 = ilwis.do('mapcalc', 'iff(@1>=0,@1,?)', rcNew2) # remove satpy nodata
rcNew2.store('msg_3_bands.mpl')

In [ ]:
print(rcNew2.size())
print(rcNew2.envelope())
rcNew2coordSys = rcNew2.coordinateSystem()
print(rcNew2coordSys.toWKT())
print(rcNew2coordSys.toProj4())

In [ ]:
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563,envelope=-5570248.4773 5570248.4773 5567248.0742 -5567248.0742,gridsize=3712 3712,cornerofcorners=yes')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0.0, 1000.0, 0.001))
b006 = ilwis.RasterCoverage()
b006.setSize(ilwis.Size(3712,3712,1))
b006.setGeoReference(grf)
b006.setDataDef(dfNum)

In [ ]:
b006.array2raster(vis006_rot.flatten())
print(b006.pix2value(ilwis.Pixel(1600,1600)))
print(b006.size())

In [ ]:
b006 = ilwis.do('mapcalc', 'iff(@1>=0,@1,?)', b006) # remove satpy nodata
b006.store('b006.mpr')

In [ ]:
b006_sub = ilwis.do('select',b006, 'boundingbox(1300 250, 1649 499)')

In [ ]:
pnew = ilwis.PropertySets.pMIN|ilwis.PropertySets.pMAX|ilwis.PropertySets.pDISTANCE|ilwis.PropertySets.pDELTA|ilwis.PropertySets.pNETTOCOUNT|ilwis.PropertySets.pCOUNT|ilwis.PropertySets.pSUM|ilwis.PropertySets.pMEAN|ilwis.PropertySets.pMEDIAN|ilwis.PropertySets.pPREDOMINANT|ilwis.PropertySets.pSTDEV|ilwis.PropertySets.pHISTOGRAM
new_stat = b006_sub.statistics(pnew)
print("Minimum:", (new_stat.prop(ilwis.PropertySets.pMIN)))
print("Maximum:", (new_stat.prop(ilwis.PropertySets.pMAX)))
print("Mean:", (new_stat.prop(ilwis.PropertySets.pMEAN)))
print("Median:", (new_stat.prop(ilwis.PropertySets.pMEDIAN)))
print("STD:", (new_stat.prop(ilwis.PropertySets.pSTDEV)))
#print("Predominant:", (new_stat.prop(ilwis.PropertySets.pPREDOMINANT))) # check predominant!!!
print("Count:", (new_stat.prop(ilwis.PropertySets.pCOUNT)))

In [ ]:
print(b006_sub.size())

In [ ]:
b006_sub.store('sub.mpr')

In [ ]:
grf_LL= ilwis.GeoReference('code=georef:type=corners, csy=epsg:4326, envelope=20 40 40 20, gridsize=600 600, cornerofcorners=yes')

In [ ]:
b006res = ilwis.do('resample', b006, grf_LL, 'nearestneighbour')
print(b006.envelope())
print(b006res.envelope())
print(b006res.size())
print(b006res.coordinateSystem())
print(b006res.coord2value(ilwis.Coordinate(30, 30))) #querying a location in lon/lat.
print(b006.coord2value(ilwis.Coordinate(2725000, 2888500))) #querying a location in original projection.
print(b006res.pix2value(ilwis.Pixel(100,100))) #querying a location in column and row
print(b006res.coord2value(ilwis.Coordinate(22.78, 5.034))) 

In [ ]:
b006res.store('b006res.mpr')

### Section on use of colour composites

In [ ]:
scn4 = Scene(reader='seviri_l1b_native', filenames=fnames)

cir = 'colorized_ir_clouds'
scn4.load([cir], upper_right_corner='NE')
scn4.show(cir)

In [ ]:
scn = Scene(reader='seviri_l1b_native', filenames=fnames)
scn.load(['colorized_ir_clouds'], upper_right_corner='NE')
scn['colorized_ir_clouds']

In [ ]:
from satpy.writers import get_enhanced_image

plt.figure(figsize=(8,8))
img = get_enhanced_image(scn['colorized_ir_clouds'])
# get DataArray out of `XRImage` object
img_data = img.data
img_data.plot.imshow(rgb='bands', vmin=0, vmax=1)

In [ ]:
data1_rot0 = np.rot90(img_data[0], k=4, axes=(1, 0))
data1_rot1 = np.rot90(img_data[1], k=4, axes=(1, 0))
data1_rot2 = np.rot90(img_data[2], k=4, axes=(1, 0))

data1_rot = np.array([data1_rot2, data1_rot1, data1_rot0]).flatten()

In [ ]:
data1 = np.array(data1_rot).flatten()

In [ ]:
print(data1.ndim)
print(data1.shape)
print(data1.size)

In [ ]:
print(len(data1))

In [ ]:
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563,envelope=-5570248.4773 5570248.4773 5567248.0742 -5567248.0742,gridsize=3712 3712,cornerofcorners=yes')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0.0, 1000.0, 0.001))
rcNew3 = ilwis.RasterCoverage()
rcNew3.setSize(ilwis.Size(3712,3712,3))
rcNew3.setGeoReference(grf)
rcNew3.setDataDef(dfNum)

In [ ]:
rcNew3.array2raster(data1)
rcNew3 = ilwis.do('mapcalc', 'iff(@1>=0,@1,?)', rcNew3) # remove satpy nodata

In [ ]:
print(rcNew3.pix2value(ilwis.Pixel(1500,2400,0)))
print(rcNew3.pix2value(ilwis.Pixel(1500,2400,1)))
print(rcNew3.pix2value(ilwis.Pixel(1500,2400,2)))

In [ ]:
print(rcNew3.size())
print(rcNew3.envelope())
rcNew3coordSys = rcNew3.coordinateSystem()
print(rcNew3coordSys.toWKT())
print(rcNew3coordSys.toProj4())

In [ ]:
rcNew3.store('cir.mpl')

#### Section on use of NWC-SAF data (format netCDF)

In [ ]:
myfiles = glob.glob(work_dir+'/S_NWC_CRR_MSG4_global-VISIR_20230117T051500Z.nc')

crr = Scene(filenames=myfiles, reader='nwcsaf-geo')
print(crr.available_composite_names())
print(crr.available_dataset_names())

In [ ]:
#get listing of other functions
dir(crr)

In [ ]:
crr.load(['convective_precipitation_hourly_accumulation', 'convective_rain_rate'])

In [ ]:
#crr.load(['convective_precipitation_hourly_accumulation'])

In [ ]:
print(crr)

In [ ]:
crr.show('convective_rain_rate')

In [ ]:
crr_load = crr['convective_rain_rate']

In [ ]:
print(crr_load)
print(crr_load.shape)

In [ ]:
crr_meas = crr_load.values

In [ ]:
print(crr_meas)
print(crr_meas.shape)

In [ ]:
plt.imshow(crr_meas, interpolation='nearest', vmin=0, vmax=11, cmap='jet')
plt.show()

In [ ]:
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563,envelope=-5570248.4773 5570248.4773 5567248.0742 -5567248.0742,gridsize=3712 3712,cornerofcorners=yes')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0.0, 1000.0, 0.00))
rcNew = ilwis.RasterCoverage()
rcNew.setSize(ilwis.Size(3712,3712,1))
rcNew.setGeoReference(grf)
rcNew.setDataDef(dfNum)

In [ ]:
rcNew.array2raster(crr_meas.flatten())
rcNew = ilwis.do('mapcalc', 'iff(@1<255,@1,?)', rcNew) # remove background - assign to no data

In [ ]:
print(rcNew.coord2value(ilwis.Coordinate(4896095.17,-1425952.85))) 

In [ ]:
rcNew.store('crr_class.mpr')

In [ ]:
crr.load(['crr_accum'])

In [ ]:
print(crr)

In [ ]:
crr.show('crr_accum')

In [ ]:
crr_meas = crr['crr_accum'].values

In [ ]:
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563,envelope=-5570248.4773 5570248.4773 5567248.0742 -5567248.0742,gridsize=3712 3712,cornerofcorners=yes')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0.0, 1000.0, 0.000))
rcNew = ilwis.RasterCoverage()
rcNew.setSize(ilwis.Size(3712,3712,1))
rcNew.setGeoReference(grf)
rcNew.setDataDef(dfNum)

In [ ]:
rcNew.array2raster(crr_meas.flatten())
rcNew = ilwis.do('mapcalc', 'iff(@1>=0,@1,?)', rcNew) # remove satpy nodata
print(rcNew.coord2value(ilwis.Coordinate(4896095.17,-1425952.85))) 

In [ ]:
rcNew.store('crr_value.mpr')

In [ ]:
myfiles1 = glob.glob(work_dir+'/S_NWC_RDT-CW_MSG4_global-VISIR_20230117T034500Z.nc')

rdt = Scene(filenames=myfiles1, reader='nwcsaf-geo')
print(rdt.available_composite_names())
print(rdt.available_dataset_names())

In [ ]:
rdt.load(['MapCellCatType', 'MapCellCatType_pal'])

In [ ]:
rdt.load(['rdt_cell_type'])

In [ ]:
print(rdt)

In [ ]:
rdt.show('rdt_cell_type')

In [ ]:
rdt_meas = rdt['rdt_cell_type'].values

In [ ]:
print(rdt_meas.shape)

In [ ]:
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563,envelope=-5570248.4773 5570248.4773 5567248.0742 -5567248.0742,gridsize=3712 3712,cornerofcorners=yes')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0.0, 1000.0, 0.000))
rcNew = ilwis.RasterCoverage()
rcNew.setSize(ilwis.Size(3712,3712,1))
rcNew.setGeoReference(grf)
rcNew.setDataDef(dfNum)

In [ ]:
rcNew.array2raster(rdt_meas.flatten())
rcNew = ilwis.do('mapcalc', 'iff(@1>0,@1,?)', rcNew) # remove no rainall (value = 0) and assign it to nodata

In [ ]:
rcNew.store('rdt_class.mpr')


Radipdly Developing Thunderstorms classes description:
+ 0=Non_convective 
+ 1=Convective_triggering 
+ 2=Convective_triggering_from_split 
+ 3=Convective_growing 
+ 4=Convective_mature 
+ 5=vershootingTop_mature 
+ 6=Convective_decaying 
+ 7=Electric_triggering 
+ 8=Electric_triggering_from_split 
+ 9=Electric_growing 
+ 10=Electric_mature 
+ 11=Electric_decaying 
+ 12=HighRainRate_triggering 
+ 13=HighRainRate_triggering_from_split 
+ 14=HighRainRate_growing 
+ 15=HighRainRate_mature 
+ 16=HighRainRate_decaying 
+ 17=HighSeverity_triggering 
+ 18=HighSeverity_triggering_from_split 
+ 19=HighSeverity_growing 
+ 20=HighSeverity_mature 
+ 21=HighSeverity_decaying
  

Review all files created using ILWIS386